# Working with Apache Iceberg tables
In this section, we will see how you can use SQL on Athena Spark to create, analyze and manage Apache Iceberg tables.

## Create database and Iceberg table
First, we will create a database in the Glue Data Catalog.

In [ ]:
%%sql
CREATE DATABASE icebergdb

Next, in the database icebergdb, we will create an iceberg table noaa_iceberg pointing to a location in S3 where we will load the data. 

**Note**: Replace the location 's3://\<your-S3-bucket\>/\<prefix\>/' to your S3 bucket and prefix:

In [ ]:
%%sql
CREATE TABLE icebergdb.noaa_iceberg(
station string, 
  date string, 
  latitude string, 
  longitude string, 
  elevation string, 
  name string, 
  temp string, 
  temp_attributes string, 
  dewp string, 
  dewp_attributes string, 
  slp string, 
  slp_attributes string, 
  stp string, 
  stp_attributes string, 
  visib string, 
  visib_attributes string, 
  wdsp string, 
  wdsp_attributes string, 
  mxspd string, 
  gust string, 
  max string, 
  max_attributes string, 
  min string, 
  min_attributes string, 
  prcp string, 
  prcp_attributes string, 
  sndp string, 
  frshtt string)
USING iceberg
PARTITIONED BY (year string)
LOCATION 's3://<your-S3-bucket>/<prefix>/noaaiceberg/'

### Insert data into table
To populate the noaa_iceberg table, we will insert data from the existing Parquet table sparkblogdb.noaa_pq that we created previously. This can be done using an INSERT INTO statement in Spark:

In [ ]:
%%sql
INSERT INTO icebergdb.noaa_iceberg select * from sparkblogdb.noaa_pq

### Querying the Iceberg table
Now that the data is inserted in the iceberg table, we can start analyzing it. Let’s run a Spark SQL to find the minimum recorded temperature for the 'SEATTLE TACOMA AIRPORT, WA US' location

In [ ]:
%%sql
select name, year, min(MIN) as minimum_temperature 
from icebergdb.noaa_iceberg
where name = 'SEATTLE TACOMA AIRPORT, WA US' 
group by 1,2

### Updating data in Iceberg table

Let's look at how to update data in our table. We want to update the station name 'SEATTLE TACOMA AIRPORT, WA US' to 'Sea-Tac'. Using Spark SQL, we can run an UPDATE statement against the Iceberg table

In [ ]:
%%sql
UPDATE icebergdb.noaa_iceberg 
SET name = 'Sea-Tac'
WHERE name = 'SEATTLE TACOMA AIRPORT, WA US'

We will run previous SELECT query to find the minimum recorded temperature for the 'Sea-Tac' location:

In [ ]:
%%sql
select name, year, min(MIN) as minimum_temperature 
from icebergdb.noaa_iceberg
where name = 'Sea-Tac' 
group by 1,2

### Compacting Data Files
More data files leads to more metadata stored in manifest files, and small data files causes an unnecessary amount of metadata and less efficient queries from file open costs. Running Iceberg’s rewrite_data_files procedure, can compact data files. This combines small files into larger files to reduce metadata overhead and runtime file open cost. For example, to run compaction on the above table, run following Spark SQL.

In [ ]:
%%sql
CALL spark_catalog.system.rewrite_data_files('icebergdb.noaa_iceberg')

### Table Snapshots:

Each write/update/delete/upsert/compaction operation on an Iceberg table creates a new snapshot of a table while keeping the old data and metadata around for snapshot isolation and time travel. To list the snapshots of an Iceberg table, run following Spark SQL statement.

In [ ]:
%%sql
SELECT * FROM spark_catalog.icebergdb.noaa_iceberg.snapshots;

### Expire Old Snapshots

Regularly expiring snapshots is recommended to delete data files that are no longer needed, and to keep the size of table metadata small. It will never remove files which are still required by a non-expired snapshot. In Athena Spark, run following SQL to expire snapshots for table icebergdb.noaa_iceberg that are older than a specific timestamp.

In [ ]:
%%sql
CALL spark_catalog.system.expire_snapshots('icebergdb.noaa_iceberg', TIMESTAMP '2023-11-30 00:00:00.000')

### Drop table and database
You can run the following Spark SQL to cleanup the Iceberg tables and associated data in S3 from this exercise:

In [ ]:
%%sql
DROP TABLE icebergdb.noaa_iceberg PURGE

Run following Spark SQL to remove the database icebergdb:

In [ ]:
%%sql
DROP DATABASE icebergdb

Dropping the table and database deletes the metadata for these objects, but does not automatically delete the data files in Amazon S3. The files can be manually deleted if no longer needed.

To learn more on what all operations can be performed on Iceberg tables using Athena Spark, please refer [Spark queries](https://iceberg.apache.org/docs/1.2.1/spark-queries/) and [Spark procedures](https://iceberg.apache.org/docs/1.2.1/spark-procedures/) section of Iceberg documentation.